In [3]:
from magent2.environments import battle_v4, adversarial_pursuit_v4, tiger_deer_v4
import sys, os
from pettingzoo.utils import random_demo
import pygame
import torch
import time
import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
from dqn_basic import DQN_Basic
from collections import namedtuple, deque
import random
import numpy as np
import matplotlib.pyplot as plt

TypeError: 'type' object is not subscriptable

In [2]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(device)
ent_coef = 0.1
vf_coef = 0.1
clip_coef = 0.1
gamma = 0.99
batch_size = 32
stack_size = 4
frame_size = (128, 128)
max_cycles = 100
total_episodes = 100
map_size = 60

env = tiger_deer_v4.env(map_size=map_size, minimap_mode=False, render_mode='human', tiger_step_recover=-0.1, deer_attacked=-0.1, max_cycles=max_cycles, extra_features=False)

# random_demo(env, render=False , episodes=1)
# 'rgb_array'
# pygame.quit()

cuda


In [3]:
class Tiger_DQN_Basic(nn.Module):
    def __init__(self, n_observations, n_actions):
        super(Tiger_DQN_Basic, self).__init__()
        self.layer1 = nn.Linear(n_observations, 128)
        self.layer2 = nn.Linear(128, 128)
        self.layer3 = nn.Linear(128, n_actions)

    # Called with either one element to determine next action, or a batch
    # during optimization. Returns tensor([[left0exp,right0exp]...]).
    def forward(self, x):
        x = F.relu(self.layer1(x))
        x = F.relu(self.layer2(x))
        return self.layer3(x)

In [4]:
class Deer_DQN_Basic(nn.Module):
    def __init__(self, n_observations, n_actions):
        super(Deer_DQN_Basic, self).__init__()
        self.layer1 = nn.Linear(n_observations, 128)
        self.layer2 = nn.Linear(128, 128)
        self.layer3 = nn.Linear(128, n_actions)

    # Called with either one element to determine next action, or a batch
    # during optimization. Returns tensor([[left0exp,right0exp]...]).
    def forward(self, x):
        x = F.relu(self.layer1(x))
        x = F.relu(self.layer2(x))
        return self.layer3(x)

In [5]:
def deer_policy(model, observation, prev_observation, no_previous=True):
    
    if no_previous:
        return torch.randint(0,model.n_actions, (1,))
    # stacked_observations = torch.cat((observation, prev_observation), 1)
    action = torch.argmax(model.forward(observation))
    # print(type(observation))
    # print(observation.shape)
    # 0 - up
    # 1 - left
    # 2 - stay still/  nothing
    # 3 - right
    # 4 - down
    # return 4
    return action

In [6]:
def tiger_policy(model, observation, prev_observation, no_previous=True):
    if no_previous:
        return torch.randint(0,model.n_actions, (1,))
    
    # stacked_observations = torch.cat((observation, prev_observation), 1)
    action = torch.argmax(model.forward(observation))
    # print(observation)
    # 0 - up
    # 1 - left
    # 2 - stay still/  nothing
    # 3 - right
    # 4 - down
    # 5 - attack up
    # 6 - attack left
    # 7 - attack right
    # 8 - attack down
    # return 5
    return action

In [ ]:
BATCH_SIZE = 128
GAMMA = 0.99
EPS_START = 0.9
EPS_END = 0.05
EPS_DECAY = 1000
TAU = 0.005
LR = 1e-4

# Get number of actions from gym action space
n_actions = env.action_space.n
# Get the number of state observations
state, info = env.reset()
n_observations = len(state)

policy_net = DQN(n_observations, n_actions).to(device) # What is this line for?
target_net = DQN(n_observations, n_actions).to(device) # Tiger or Deer?
target_net.load_state_dict(policy_net.state_dict())

optimizer = optim.AdamW(policy_net.parameters(), lr=LR, amsgrad=True)
memory = ReplayMemory(10000) # is this line needed?
Transition = namedtuple('Transition',
                        ('state', 'action', 'next_state', 'reward'))

In [7]:
def optimize_model(episode_data, model):
    if len(episode_data) < batch_size:
        return
    optimizer.zero_grad()
    batch = random.sample(episode_data, batch_size)
    state_batch, action_batch, reward_batch, next_state_batch, done_batch = map(np.array, zip(*batch))

    # Find a way to add the masked observations to the state_batch
    # state_batch = torch.cat((state_batch, masked_observations), 1)
    # next_state_batch = torch.cat((next_state_batch, masked_observations), 1)
    
    # # Compute a mask of non-final states and concatenate the batch elements
    # # (a final state would've been the one after which simulation ended)
    # non_final_mask = torch.tensor(tuple(map(lambda s: s is not None,
    #                                       batch.next_state)), device=device, dtype=torch.bool)
    # non_final_next_states = torch.cat([s for s in batch.next_state
    #                                             if s is not None])
    # state_batch = torch.cat(batch.state)
    # action_batch = torch.cat(batch.action)
    # reward_batch = torch.cat(batch.reward)

    state_batch = torch.tensor(state_batch, dtype=torch.float32, device=device)
    action_batch = torch.tensor(action_batch, dtype=torch.int64, device=device)
    reward_batch = torch.tensor(reward_batch, dtype=torch.float32, device=device)
    next_state_batch = torch.tensor(next_state_batch, dtype=torch.float32, device=device)
    done_batch = torch.tensor(done_batch, dtype=torch.float32, device=device)

    # Compute Q(s_t, a) - the model computes Q(s_t), then we select the
    # columns of actions taken. These are the actions which would've been taken
    # for each batch state according to policy_net
    state_action_values = model(state_batch).gather(1, action_batch.unsqueeze(1))

    # Compute V(s_{t+1}) for all next states.
    # Expected values of actions for non_final_next_states are computed based
    # on the "older" target_net; selecting their best reward with max(1)[0].
    # This is merged based on the mask, such that we'll have either the expected
    # state value or 0 in case the state was final.
    next_state_values = torch.zeros(batch_size, device=device)
    next_state_values[done_batch == 0] = model(next_state_batch[done_batch == 0]).max(1)[0].detach()

    # Compute the expected Q values
    expected_state_action_values = (next_state_values * GAMMA) + reward_batch
    
    # Compute Huber loss
    loss = F.smooth_l1_loss(state_action_values, expected_state_action_values.unsqueeze(1))

    # Optimize the model
    loss.backward()
    for param in model.parameters():
        param.grad.data.clamp_(-1, 1)
    optimizer.step()

In [8]:
def generate_plots(episode_data):
    # number of deer
    # number of tigers
    # average life?
    
    pass

In [9]:
def mask_observations(agent,agents_prev_data,observation):
    maskDeer=torch.tensor([ [1,1,1],
                            [1,1,1],
                            [0,0,0],
                            ])
    deerOpt=[0,1,0,3,2]
    maskTiger=torch.tensor([[1,1,1,1,1,1,1,1,1],
                            [1,1,1,1,1,1,1,1,1],
                            [1,1,1,1,1,1,1,1,1],
                            [1,1,1,1,1,1,1,1,1],
                            [1,1,1,1,1,1,1,1,1],
                            [1,1,1,1,1,1,1,1,1],
                            [0,0,0,0,0,0,0,0,0],
                            [0,0,0,0,0,0,0,0,0],
                            [0,0,0,0,0,0,0,0,0],
                            ])
    tigerOpt=[0,1,0,3,2,0,1,3,2]
    rotCount=0
    if 'tiger' in agent:
        if agents_prev_data[agent][5] is None:
            rotCount=0
        else:
            rotCount=tigerOpt[agents_prev_data[agent][5]]
        finalMask=maskTiger
        maskedObs=observation
        for i in range(rotCount):
            finalMask=torch.rot90(finalMask, 1, [0, 1])
        for i in range(observation.shape[3]):
            maskedObs[:,:,:,i]=maskedObs[:,:,:,i]*finalMask
        return maskedObs
    else:
        if agents_prev_data[agent][5] is None:
            rotCount=0
        else:
            rotCount=deerOpt[agents_prev_data[agent][5]]
        finalMask=maskDeer
        maskedObs=observation
        for i in range(rotCount):
            finalMask=torch.rot90(finalMask, 1, [0, 1])
        for i in range(observation.shape[3]):
            maskedObs[:,:,:,i]=maskedObs[:,:,:,i]*finalMask
        return maskedObs
        

In [10]:
def get_agent_type_from_agent_name(agent):
    if 'tiger' in agent:
        return 'tiger'
    return 'deer'

In [12]:
tiger_model = DQN_Basic((9,9,5), 9)
deer_model = DQN_Basic((3,3,5), 5)
# tiger_model.to(device=device)
# deer_model.to(device=device)
agents_prev_data = {}
for episodes in range(total_episodes):
    env.reset(seed=None)
    episode_data = {'deer': [], 'tiger':[]}
    for agent in env.agent_iter():

        observation, reward, termination, truncation, info = env.last()
        observation = torch.unsqueeze(torch.from_numpy(observation),0)
        
        # instantiate previous data
        no_previous = False
        if agent not in agents_prev_data.keys():
            agents_prev_data[agent] = [None]*6
            no_previous = True

        prev_observation = agents_prev_data[agent][0]

        # set agent type to tiger or deer based on agentName
        agentType = get_agent_type_from_agent_name(agent)
        print(observation[:,:,:,0])
        print(mask_observations(agent,agents_prev_data,observation)[:,:,:,0])
        # input()
        # catch if agent is dead
        done = termination or truncation

        if not done:
            # if the agent is not dead
            if 'tiger' in agent:
                action =  tiger_policy(tiger_model, observation, prev_observation, no_previous=no_previous)
            else:
                action = deer_policy(deer_model, observation, prev_observation, no_previous=no_previous)
            episode_data[agentType].append([agent, observation, reward, termination, truncation, info, action])
        else:
            # if agent is dead
            action = None
        if isinstance(action, torch.Tensor):
            action = action.item()
        # previous recorded data
        agents_prev_data[agent] = [observation, reward, termination, truncation, info, action]
        env.step(action)

    #########################
    # plots for data
    generate_plots(episode_data)
    #########################
    optimize_model(episode_data['deer'], deer_model)
    optimize_model(episode_data['tiger'], tiger_model)
env.close()

tensor([[[0., 0., 0.],
         [0., 0., 0.],
         [0., 0., 0.]]])
tensor([[[0., 0., 0.],
         [0., 0., 0.],
         [0., 0., 0.]]])
tensor([[[0., 0., 0.],
         [0., 0., 0.],
         [0., 0., 0.]]])
tensor([[[0., 0., 0.],
         [0., 0., 0.],
         [0., 0., 0.]]])
tensor([[[0., 0., 0.],
         [0., 0., 0.],
         [0., 0., 0.]]])
tensor([[[0., 0., 0.],
         [0., 0., 0.],
         [0., 0., 0.]]])
tensor([[[0., 0., 0.],
         [0., 0., 0.],
         [0., 0., 0.]]])
tensor([[[0., 0., 0.],
         [0., 0., 0.],
         [0., 0., 0.]]])
tensor([[[0., 0., 0.],
         [0., 0., 1.],
         [0., 1., 0.]]])
tensor([[[0., 0., 0.],
         [0., 0., 1.],
         [0., 0., 0.]]])
tensor([[[0., 1., 0.],
         [0., 0., 0.],
         [0., 0., 0.]]])
tensor([[[0., 1., 0.],
         [0., 0., 0.],
         [0., 0., 0.]]])
tensor([[[0., 0., 0.],
         [0., 0., 0.],
         [0., 0., 0.]]])
tensor([[[0., 0., 0.],
         [0., 0., 0.],
         [0., 0., 0.]]])
tensor

d:\TempSync\CS7643\The-Learning-Shoal\src\tests\dqn_basic.py:34: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  x = self.softmax(x)


tensor([[[0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 1., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 1., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0.]]])
tensor([[[0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 1., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 1., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 1., 0., 0., 0., 0.]]])
tensor([[[0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0.],
         

KeyboardInterrupt: 

In [ ]:
print(env.action_space)
print(type(env))
print(env.num_agents)
print(env.possible_agents)
print(env.action_spaces)

<bound method BaseWrapper.action_space of <pettingzoo.utils.wrappers.order_enforcing.OrderEnforcingWrapper object at 0x0000019EA51758D0>>
<class 'pettingzoo.utils.wrappers.order_enforcing.OrderEnforcingWrapper'>
0
['deer_0', 'deer_1', 'deer_2', 'deer_3', 'deer_4', 'deer_5', 'deer_6', 'deer_7', 'deer_8', 'deer_9', 'deer_10', 'deer_11', 'deer_12', 'deer_13', 'deer_14', 'deer_15', 'deer_16', 'deer_17', 'deer_18', 'deer_19', 'deer_20', 'deer_21', 'deer_22', 'deer_23', 'deer_24', 'deer_25', 'deer_26', 'deer_27', 'deer_28', 'deer_29', 'deer_30', 'deer_31', 'deer_32', 'deer_33', 'deer_34', 'deer_35', 'deer_36', 'deer_37', 'deer_38', 'deer_39', 'deer_40', 'deer_41', 'deer_42', 'deer_43', 'deer_44', 'deer_45', 'deer_46', 'deer_47', 'deer_48', 'deer_49', 'deer_50', 'deer_51', 'deer_52', 'deer_53', 'deer_54', 'deer_55', 'deer_56', 'deer_57', 'deer_58', 'deer_59', 'deer_60', 'deer_61', 'deer_62', 'deer_63', 'deer_64', 'deer_65', 'deer_66', 'deer_67', 'deer_68', 'deer_69', 'deer_70', 'deer_71', 'de

c:\Users\mike\AppData\Local\Programs\Python\Python310\lib\site-packages\pettingzoo\utils\wrappers\base.py:64: UserWarning: The `action_spaces` dictionary is deprecated. Use the `action_space` function instead.
  warnings.warn(
